# Alinhamento de Preferências com Otimização de Preferências de Razão de Chances (ORPO)

Este caderno o guiará pelo processo de ajuste fino de um modelo de linguagem usando a Otimização de Preferências de Razão de Chances (ORPO). Usaremos o modelo SmolLM2-135M que **não** passou pelo treinamento do SFT, portanto, não é compatível com o DPO. Isso significa que você não pode usar o modelo que treinou em [1_instruction_tuning](../../1_instruction_tuning/notebooks/sft_finetuning_example.ipynb).

<div style='background-color: lightblue; padding: 10px; border-radius: 5px; margin-bottom: 20px; color:black'>
     <h2 style='margin: 0;color:blue'>Exercício: Alinhamento do SmolLM2 com o DPOTrainer</h2>
     <p>Pegue um conjunto de dados do hub do Hugging Face e alinhe um modelo a ele. </p> 
     <p><b>Níveis de Dificuldade</b></p>
     <p>🐢 Use o conjunto de dados `trl-lib/ultrafeedback_binarized`.</p>
     <p>🐕 Experimente usar o conjunto de dados `argilla/ultrafeedback-binarized-preferences.</p>
     <p>🦁 Experimente usar um subconjunto do conjunto de dados `orpo-dpo-mix-40k` de mlabonne.</p>
</div>



## Importe os módulos


In [ ]:
import torch
import os
from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
)
from trl import ORPOConfig, ORPOTrainer, setup_chat_format

# Authenticate to Hugging Face
from huggingface_hub import login

login()

/Users/ben/code/smol-course/.venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Formate o conjunto de dados

In [ ]:
# Load dataset

# TODO: 🦁🐕 change the dataset to one of your choosing
dataset = load_dataset(path="trl-lib/ultrafeedback_binarized")

Generating test split: 100%|██████████| 1000/1000 [00:00<00:00, 382866.64 examples/s]


In [ ]:
# TODO: 🐕 If your dataset is not represented as conversation lists, you can use the `process_dataset` function to convert it.

## Defina o modelo

In [ ]:
model_name = "HuggingFaceTB/SmolLM2-135M"

device = (
    "cuda"
    if torch.cuda.is_available()
    else "mps" if torch.backends.mps.is_available() else "cpu"
)

# Model to fine-tune
model = AutoModelForCausalLM.from_pretrained(
    pretrained_model_name_or_path=model_name,
    torch_dtype=torch.float16,
).to(device)
model.config.use_cache = False
tokenizer = AutoTokenizer.from_pretrained(model_name)
model, tokenizer = setup_chat_format(model, tokenizer)

# Set our name for the finetune to be saved &/ uploaded to
finetune_name = "SmolLM2-FT-DPO"
finetune_tags = ["smol-course", "module_1"]

## Treine o modelo com ORPO

In [ ]:
orpo_args = ORPOConfig(
    # Small learning rate to prevent catastrophic forgetting
    learning_rate=8e-6,
    # Linear learning rate decay over training
    lr_scheduler_type="linear",
    # Maximum combined length of prompt + completion
    max_length=1024,
    # Maximum length for input prompts
    max_prompt_length=512,
    # Controls weight of the odds ratio loss (λ in paper)
    beta=0.1,
    # Batch size for training
    per_device_train_batch_size=2,
    per_device_eval_batch_size=2,
    # Helps with training stability by accumulating gradients before updating
    gradient_accumulation_steps=4,
    # Memory-efficient optimizer for CUDA, falls back to adamw_torch for CPU/MPS
    optim="paged_adamw_8bit" if device == "cuda" else "adamw_torch",
    # Number of training epochs
    num_train_epochs=1,
    # When to run evaluation
    evaluation_strategy="steps",
    # Evaluate every 20% of training
    eval_steps=0.2,
    # Log metrics every step
    logging_steps=1,
    # Gradual learning rate warmup
    warmup_steps=10,
    # Disable external logging
    report_to="none",
    # Where to save model/checkpoints
    output_dir="./results/",
    # Enable MPS (Metal Performance Shaders) if available
    use_mps_device=device == "mps",
    hub_model_id=finetune_name,
)

In [ ]:
trainer = ORPOTrainer(
    model=model,
    args=orpo_args,
    train_dataset=dataset["train"],
    eval_dataset=dataset["test"],
    processing_class=tokenizer,
)

In [ ]:
trainer.train()  # Train the model

# Save the model
trainer.save_model(f"./{finetune_name}")

# Save to the huggingface hub if login (HF_TOKEN is set)
if os.getenv("HF_TOKEN"):
    trainer.push_to_hub(tags=finetune_tags)

## 💐 Você terminou!

Este caderno forneceu um guia passo-a-passo para o ajuste fino do modelo `HuggingFaceTB/SmolLM2-135M` usando o `ORPOTrainer`. Seguindo essas etapas, você pode adaptar o modelo para executar tarefas específicas com mais eficiência. Se quiser continuar trabalhando neste curso, aqui estão as etapas que você pode experimentar:

- Experimente este notebook em uma dificuldade maior
- Revisar o PR de um colega
- Melhorar o material do curso por meio de uma Issue ou PR.